In [ ]:
import ee
ee.Initialize()

import numpy as np
from shapely.geometry import Point, mapping, Polygon
import pandas as pd, geopandas as gpd
import json, os

crs = ee.Projection('EPSG:4326')

In [ ]:
def create_ee_fc(fid):
    '''
    Turn a geopandas dataframe into an earth engine feature collection
    '''
    gdf = gpd.read_file(fid)
    geo_json = gdf.to_json()
    ee_samp = ee.FeatureCollection(json.loads(geo_json))
    return ee_samp

def create_ee_fc_split(fid, n_chunks=20):
    '''
    Turn a geopandas dataframe into a set of earth engine feature collections.
    Useful for very large data sets.
    '''

    gdf = gpd.read_file(fid)
    dflist = np.array_split(gdf, n_chunks)
    out_fc_list = []
    for df in dflist:
        geo_json = df.to_json()
        ee_samp = ee.FeatureCollection(json.loads(geo_json))
        out_fc_list.append(ee_samp)
    return out_fc_list

In [ ]:
def reduce_res(ic, out_crs, scale, agg_fx):
    '''
    Simple resolution reducer based on some aggregation function
    '''
    def red_(image):
        reduce_image = image.reduceResolution(reducer=agg_fx, maxPixels=65535)
        return reduce_image.reproject(crs=out_crs, scale=scale).set('system:time_start', image.get('system:time_start'))
    return ic.map(red_)

def kNDVI(image):
    '''
    Add a kNDVI band to an image
    '''
    ndvi2 = image.pow(2)
    kndvi = ndvi2.tan()
    return kndvi.set('system:time_start', image.get('system:time_start'))

def rescale(ic, scale, add=0):
    '''
    Rescale all images in an image collection by a given scale factor and addative factor. 
    ASSUMES ALL BANDS SCALED EQUALLY
    '''
    def r(image):
        return image.multiply(scale).add(add).set('system:time_start', image.get('system:time_start'))
    return ic.map(r)

def mask_images(ic, maskband, maskbit):
    '''
    Quick and dirty masking for MODIS data (or other simple contexts where the first QA bit is general)
    '''
    def mask_(image):
        qc = (1 << maskbit) #Bit 0 is the general quality flag
        qa = image.select(maskband) #Get the pixel QA band.
        mask = qa.bitwiseAnd(qc).eq(0)
        return image.updateMask(mask)
    return ic.map(mask_)

In [ ]:
#Load in data and remove low-quality measurements
ds, de = '2000-10-01', '2022-10-01' #Second date is EXCLUSIVE, match start of resampled RAD to LST/NDVI

MOD13_250 = ee.ImageCollection("MODIS/061/MOD13Q1").filterDate(ds, de) #THIS IS 250m DATA
MOD13_250_hq = mask_images(MOD13_250, 'SummaryQA', 0)
evi_250 = MOD13_250_hq.select('EVI')
evi_250 = rescale(evi_250, 0.0001)
ndvi_250 = MOD13_250_hq.select('NDVI')
ndvi_250 = rescale(ndvi_250, 0.0001)
kndvi_250 = ndvi_250.map(kNDVI)

MOD13_1k = ee.ImageCollection("MODIS/061/MOD13A2").filterDate(ds, de) #THIS IS 1KM DATA
MOD13_1k_hq = mask_images(MOD13_1k, 'SummaryQA', 0)
evi_1k = MOD13_1k_hq.select('EVI')
evi_1k = rescale(evi_1k, 0.0001)
ndvi_1k = MOD13_1k_hq.select('NDVI')
ndvi_1k = rescale(ndvi_1k, 0.0001)
kndvi_1k = ndvi_1k.map(kNDVI)

crs = ee.Projection('EPSG:4326')
mod_crs = ndvi_250.first().projection() #Use this coordinate system for the spatial aggregation

evi_5k = reduce_res(evi_1k, mod_crs, 5000, ee.Reducer.mean())
ndvi_5k = reduce_res(ndvi_1k, mod_crs, 5000, ee.Reducer.mean())
kndvi_5k = reduce_res(kndvi_1k, mod_crs, 5000, ee.Reducer.mean())

evi_10k = reduce_res(evi_1k, mod_crs, 10000, ee.Reducer.mean())
ndvi_10k = reduce_res(ndvi_1k, mod_crs, 10000, ee.Reducer.mean())
kndvi_10k = reduce_res(kndvi_1k, mod_crs, 10000, ee.Reducer.mean())

evi_25k = reduce_res(evi_1k, mod_crs, 25000, ee.Reducer.mean())
ndvi_25k = reduce_res(ndvi_1k, mod_crs, 25000, ee.Reducer.mean())
kndvi_25k = reduce_res(kndvi_1k, mod_crs, 25000, ee.Reducer.mean())

In [ ]:
def stable_lc():
    '''Generate stable land cover mask'''
    start = ee.ImageCollection('MODIS/061/MCD12Q1').filterDate('2001-01-01', '2001-12-31').first().select('LC_Type1')
    for yr in range(2002,2021):
        sy = str(yr)
        dataset = ee.ImageCollection('MODIS/061/MCD12Q1').filterDate(sy + '-01-01', sy + '-12-31')
        igbpLandCover = dataset.first().select('LC_Type1')
        mask = igbpLandCover.eq(start)
        start = start.updateMask(mask)
    
    #start = start.where(start.eq(17), -1) #Optional further water mask
    mask = start.lt(11) #Perm wetlands, croplands, urban, snow, barren, water REMOVED
    #mask3 = image.eq(11) #Perm wetlands
    #mask4 = image.eq(15) #Perm snow and ice
    #mask5 = image.eq(16) #Barren
    #mask6 = image.eq(17) #Water Bodies
    
    final_lc = start.updateMask(mask)
    
    return final_lc.set('system:time_start', start.get('system:time_start'))

In [ ]:
def export_timeseries_multiFeature(collection, filename, features, scale, crs=None, folder=None, \
                                   agg_fx=ee.Reducer.mean(), extra_atts = []):
    '''
    Runs an export function on GEE servers. Exports large amounts of time series data
    '''
    if not crs:
        crs = ee.Projection('EPSG:4326')

    #Create the time series    
    def createTS(image):
        date = image.get('system:time_start')
        vals = image.reduceRegions(features, agg_fx, scale, crs)#, properties=['fid'])
        
        def set_date(f):
            return f.set('date', ee.Date(date).format('Y/M/d'))
        
        vals = vals.map(set_date)
        
        return vals
    
    TS = collection.map(createTS).flatten()
    
    if agg_fx == ee.Reducer.mean(): #NOTE: THIS NEEDS TO BE EXPANDED FOR OTHER CASES
        agg = 'mean'
        
    slist = ['date', agg, 'fid']
    for i in extra_atts:
        slist.append(i) #Can save extra attributes from the feature collection if needed (e.g., other metadata)
    
    task_config = {'description': filename, 'fileFormat': 'CSV', 'selectors': slist}
    if folder:
        task_config['folder'] = folder
    task = ee.batch.Export.table.toDrive(TS, **task_config)
    task.start()

In [ ]:
numpts = 10000 #10 land covers, 100,000 samples
minx, maxx = -180, 180
miny, maxy = -60, 80
big_area = Polygon([[minx, maxy], [maxx, maxy], [maxx, miny], [minx, miny]])
polygon = gee_geometry_from_shapely(big_area)
new_samp = False #Location of previously calculated random sample

if new_samp:
    slc = stable_lc() #Get stable land cover
    strat_samp = slc.stratifiedSample(numpts, dropNulls=True, geometries=True, region=polygon, seed=0).map(fix_atts)
    export_features(strat_samp, 'StratSamp_MODLC_n100000', folder='Strat_100k', output_format='geoJSON')
    #Now use those features to get time series
    export_timeseries_multiFeature(evi_250, 'EVI_StratSamp_MODLC_n10000', strat_samp, 250, crs=crs, folder='Strat_1mil')
    #... so on for other spatial resolutions
else:
    #If there is already a random selection done, load it
    strat_samp = create_ee_fc(new_samp)
    ee_fcs = create_ee_fc_split(new_samp, n_chunks=20)
    rdic = {'250m':250, '1k':1000, '5k':5000, '10k':10000, '25k':25000}

    for i, fc in enumerate(ee_fcs):
        #Example for all spatial resolutions and data  types
        export_timeseries_multiFeature(ndvi_250, 'NDVI_StratSamp_MODLC_n10000_n' + str(i) + '_250m', fc, 250, crs=crs, folder='NDVI_MODLC_250m')
        export_timeseries_multiFeature(ndvi_1k, 'NDVI_StratSamp_MODLC_n10000_n' + str(i) + '_1k', fc, 1000, crs=crs, folder='NDVI_MODLC_1k')
        export_timeseries_multiFeature(ndvi_5k, 'NDVI_StratSamp_MODLC_n10000_n' + str(i) + '_5k', fc, 5000, crs=crs, folder='NDVI_MODLC_5k')
        export_timeseries_multiFeature(ndvi_10k, 'NDVI_StratSamp_MODLC_n10000_n' + str(i) + '_10k', fc, 10000, crs=crs, folder='NDVI_MODLC_10k')
        export_timeseries_multiFeature(ndvi_25k, 'NDVI_StratSamp_MODLC_n10000_n' + str(i) + '_25k', fc, 25000, crs=crs, folder='NDVI_MODLC_25k')

        export_timeseries_multiFeature(kndvi_250, 'kNDVI_StratSamp_MODLC_n10000_n' + str(i) + '_250m', fc, 250, crs=crs, folder='kNDVI_MODLC_250m')
        export_timeseries_multiFeature(kndvi_1k, 'kNDVI_StratSamp_MODLC_n10000_n' + str(i) + '_1k', fc, 1000, crs=crs, folder='kNDVI_MODLC_1k')
        export_timeseries_multiFeature(kndvi_5k, 'kNDVI_StratSamp_MODLC_n10000_n' + str(i) + '_5k', fc, 5000, crs=crs, folder='kNDVI_MODLC_5k')
        export_timeseries_multiFeature(kndvi_10k, 'kNDVI_StratSamp_MODLC_n10000_n' + str(i) + '_10k', fc, 10000, crs=crs, folder='kNDVI_MODLC_10k')
        export_timeseries_multiFeature(kndvi_25k, 'kNDVI_StratSamp_MODLC_n10000_n' + str(i) + '_25k', fc, 25000, crs=crs, folder='kNDVI_MODLC_25k')

        export_timeseries_multiFeature(evi_250, 'EVI_StratSamp_MODLC_n10000_n' + str(i) + '_250m', fc, 250, crs=crs, folder='EVI_MODLC_250m')
        export_timeseries_multiFeature(evi_1k, 'EVI_StratSamp_MODLC_n10000_n' + str(i) + '_1k', fc, 1000, crs=crs, folder='EVI_MODLC_1k')
        export_timeseries_multiFeature(evi_5k, 'EVI_StratSamp_MODLC_n10000_n' + str(i) + '_5k', fc, 5000, crs=crs, folder='EVI_MODLC_5k')
        export_timeseries_multiFeature(evi_10k, 'EVI_StratSamp_MODLC_n10000_n' + str(i)+ '_10k', fc, 10000, crs=crs, folder='EVI_MODLC_10k')
        export_timeseries_multiFeature(evi_25k, 'EVI_StratSamp_MODLC_n10000_n' + str(i) + '_25k', fc, 25000, crs=crs, folder='EVI_MODLC_25k')

In [ ]:
def prep_file(fid):
    '''
    Read in the exported data files and turn them into single time series objects for further use.
    '''
    data = pd.read_csv(fid)
    gb = data.groupby('fid')
    sers = {}
    for g in gb:
        if not eco:
            idnr = g[0]
        else:
            idn, eid = g[0]
            idnr = str(eid) + '_' + str(idn) 
        date = g[1].date
        val = g[1]['mean'].values
        date = [pd.Timestamp(x) for x in date]
        ser = pd.Series(val, index=date)
        sers[idnr] = ser
    return sers